## Import Libraries

### General

In [1]:
import pandas as pd
from datasets import Dataset
import numpy as np
import os
os.environ["WANDB_DISABLED"] = "true"

### Training

In [2]:
import torch
from transformers import AutoModelForSequenceClassification, Trainer, TrainingArguments, DataCollatorWithPadding, AutoTokenizer, TrainerCallback
from torch.nn.functional import softmax

2025-02-16 05:12:27.009277: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
import torch.nn as nn
import torch.nn.functional as F

In [4]:
import matplotlib.pyplot as plt

### Metrics

In [5]:
from sklearn.metrics import accuracy_score, classification_report, roc_auc_score, roc_curve

### Config

In [6]:
pd.set_option('display.max_rows', 20)  
pd.set_option('display.max_columns', 20) 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)
print("CUDA available:", torch.cuda.is_available())
print("GPU Name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "No GPU detected")


Using device: cuda
CUDA available: True
GPU Name: NVIDIA GeForce RTX 3050 Ti Laptop GPU


## Preprocessing

In [7]:
df = pd.read_csv('super_sms_dataset.csv', encoding='latin-1')
df['label'] = df['Labels'].fillna(0)
df['text'] = df['SMSes'].astype(str).dropna()
df = df[['text', 'label']]

df.iloc[:, [0, 1]] = df.iloc[:, [1, 0]].values
df.columns = ['label', 'text']
df['label']=df['label'].astype(int)
df

/tmp/ipykernel_524431/4286418111.py:6: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '['There be an update for your delivery CC 01728161E due 09.06.2020 Tap here http://olo.me/3i6xF', 'watch your favorite english movies of all genre like fast  furious  the thaw stepup  in just rs month to subscribe give a miss call on +91XXXXXXX ', 'aur what is the status for fms', 'hi shalini sundi thank you for dialling  special offer for you is talk to stars to subscribe  dial toll free now', 'm tryin to understand too...', 'vip number for sale   rs  cont kumar ', 'Hee. Muacks. Love u dear!', 'This be a reminder that your package will be deliver only when we receive the $57 pending amount', 'Whoops let me convert it', 'whats going on mate ?', "Hey it's Joe We're doing 100 k for 116 k and LOC unsecured. What's your email?", ' flat off vlcc weight loss facial trt hair trt  laser figure tummy thigh hips correction trt lose  kgs  hai

label                                               text
0          1  There be an update for your delivery CC 017281...
1          1  watch your favorite english movies of all genr...
2          0                     aur what is the status for fms
3          1  hi shalini sundi thank you for dialling  speci...
4          0                       m tryin to understand too...
...      ...                                                ...
67005      0                Haha sorry I will be arriving late.
67006      0  Not going out today something cropped up I am ...
67007      0  No no I didn't decide not to turn up I oversle...
67008      0                             Spring apartment homes
67009      0   Okk find u in morning I slpin at discussion rm 2

[67010 rows x 2 columns]

In [8]:
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

dataset = Dataset.from_pandas(df)

def tokenize_data(batch):
    return tokenizer(batch["text"],
                     padding="max_length",
                     truncation=True,
                     max_length=128)

tokenized_dataset = dataset.map(tokenize_data, batched=True)
tokenized_dataset

/home/mirza-mohammad-azwad/anaconda3/envs/biponon/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Map:   0%|          | 0/67010 [00:00<?, ? examples/s]

Dataset({
    features: ['label', 'text', 'input_ids', 'attention_mask'],
    num_rows: 67010
})

In [9]:
from sklearn.model_selection import train_test_split

# Convert dataset to a DataFrame (if not already)
df = tokenized_dataset.to_pandas()

# Split dataset into 80% train, 20% test
train_texts, test_texts, train_labels, test_labels = train_test_split(
    df["text"], df["label"], test_size=0.2, random_state=42
)


## Training Models

In [10]:

model = AutoModelForSequenceClassification.from_pretrained("distilbert-base-uncased", num_labels=2).to(device)

# Prepare training and testing datasets (Hugging Face Datasets)
train_data = tokenized_dataset.select(train_texts.index)
train_data = train_data.remove_columns(["text"]) # Remove unnecessary text column
test_data = tokenized_dataset.select(test_texts.index)
test_data = test_data.remove_columns(["text"])  # Remove unnecessary text column

teacher_training_args = TrainingArguments(
    output_dir="./teacher_results",
    evaluation_strategy="epoch",
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir="./teacher_logs",
    save_total_limit=1,
    fp16=True
)

# Set up the Data Collator for padding the sequences
data_collator = DataCollatorWithPadding(tokenizer)  # Use DataCollatorWithPadding

# Define Trainer
teacher_trainer = Trainer(
    model=model,
    args=teacher_training_args,
    train_dataset=train_data,
    eval_dataset=test_data,
    data_collator=data_collator,
    tokenizer=tokenizer
)
print(f"Trainer will use device: {teacher_trainer.args.device}")

# Train teacher model
teacher_trainer.train()

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_layer_norm.bias', 'vocab_projector.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight', 'vocab_transform.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.bias', 'pre_classifier.bias', 'classifier.we

Trainer will use device: cuda:0


  0%|          | 0/10053 [00:00<?, ?it/s]

You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
/home/mirza-mohammad-azwad/anaconda3/envs/biponon/lib/python3.10/site-packages/transformers/trainer.py:2664: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  else torch.cuda.amp.autocast(cache_enabled=cache_enabled, dtype=self.amp_dtype)


{'loss': 0.0703, 'learning_rate': 4.75281010643589e-05, 'epoch': 0.15}


...

{'loss': 0.0119, 'learning_rate': 2.984183825723665e-07, 'epoch': 2.98}


/home/mirza-mohammad-azwad/anaconda3/envs/biponon/lib/python3.10/site-packages/transformers/trainer.py:2664: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  else torch.cuda.amp.autocast(cache_enabled=cache_enabled, dtype=self.amp_dtype)


  0%|          | 0/838 [00:00<?, ?it/s]

{'eval_loss': 0.02865550108253956, 'eval_runtime': 34.4597, 'eval_samples_per_second': 388.918, 'eval_steps_per_second': 24.318, 'epoch': 3.0}
{'train_runtime': 1730.5417, 'train_samples_per_second': 92.933, 'train_steps_per_second': 5.809, 'train_loss': 0.02286458884639241, 'epoch': 3.0}


TrainOutput(global_step=10053, training_loss=0.02286458884639241, metrics={'train_runtime': 1730.5417, 'train_samples_per_second': 92.933, 'train_steps_per_second': 5.809, 'train_loss': 0.02286458884639241, 'epoch': 3.0})

## Evaluation

In [ ]:
# Convert tokenized dataset labels to tensors and move them to the same device
labels = torch.tensor(test_labels.tolist()).to(device)
test_data = tokenized_dataset.select(test_texts.index)
# Get predictions from the model
preds = teacher_trainer.predict(test_data)
pred_labels = torch.tensor(preds.predictions.argmax(-1)).to(device)
pred_probs = torch.tensor(preds.predictions[:, 1]).to(device)  # Ensure probabilities are on the same device

# Compute accuracy
accuracy = accuracy_score(labels.cpu(), pred_labels.cpu())
print(f"DistilBERT Accuracy: {accuracy:.6f}")

# Show classification report
print(classification_report(labels.cpu(), pred_labels.cpu(), digits=6))

# Compute ROC curve and AUC
fpr, tpr, thresholds = roc_curve(labels.cpu(), pred_probs.cpu())
auc = roc_auc_score(labels.cpu(), pred_probs.cpu())
print(f"DistilBERT AUC: {auc:.6f}")

# Plot ROC curve
plt.figure(figsize=(10, 6))
plt.plot(fpr, tpr, color='blue', label=f'AUC = {auc:.6f}')
plt.plot([0, 1], [0, 1], color='gray', linestyle='--')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('ROC Curve for DistilBERT')
plt.legend(loc='lower right')
plt.grid()
plt.show()

  0%|          | 0/838 [00:00<?, ?it/s]

DistilBERT Accuracy: 0.994031
              precision    recall  f1-score   support

           0   0.994727  0.995460  0.995093      8149
           1   0.992948  0.991814  0.992381      5253

    accuracy                       0.994031     13402
   macro avg   0.993838  0.993637  0.993737     13402
weighted avg   0.994030  0.994031  0.994030     13402

DistilBERT AUC: 0.999333


: 